In [2]:
import re
import numpy as np
import pandas as pd
from pprint import pprint
import gensim, spacy, logging, warnings
import gensim.corpora as corpora
from gensim.utils import simple_preprocess
from gensim.models import CoherenceModel, LdaModel
import matplotlib.pyplot as plt
from nltk.corpus import stopwords
from gensim import corpora
from gensim import models
from gensim.models import CoherenceModel
from langid import set_languages, classify
set_languages(['nl', 'en'])

from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.cluster import KMeans
from sklearn.manifold import TSNE
from bokeh.plotting import figure, show, output_notebook
from bokeh.io import push_notebook
import matplotlib.pyplot as plt
import matplotlib.colors as mcolors

from bertopic import BERTopic
from umap import UMAP 
from sentence_transformers import SentenceTransformer

# 5. Embedding and visualising GWF


This embeds the Grote Word File. To then inspect the clusters.

# Get dataset

In [7]:
df_grote_word_doc = pd.read_json(r'C:\Users\johan\Documents\GitHub\sandbox\NLP\data\NLP for grote word-filev2.json')

# stopwords

In [4]:
from nltk.corpus import stopwords

stop_words = stopwords.words('dutch') + stopwords.words('english') 

# more_words = ['vooral', 'gaan', 'één', 'value', 'part', 'use', 'blijven', 'waarbij', 'stuk', 'wanneer', 'much', 'kennen', 'always', 'tegelijk', 'however', 'geven', 'nooit', 'weg', 'vaak', 'soort', 'wellicht', 'leggen', 'steken', 'leven', 'zoal,', 'waar', 'allemaal', 'net', 'eigen', 'stefaf', 'vallen', 'zaak', 'feit', 'waaruit', 'zelfs', 'year', 'echter', 'zien', 'come', 'willen', 'spreken', 'straf', 'lijken', 'staan', 'even', 'hoog', 'pas', 'liggen', 'waarom', 'helemaal', 'situatie', 'waaraan', 'zitten', 'take', 'waarin', 'often', 'wel', 'maken', 'nieuw', 'waarop', 'plots', 'say', 'goed', 'way', 'terug', 'mogelijk', 'many', 'daarom', 'omwille', 'leren', 'nemen', 'kijken', 'waarde', 'gebruiken', 'iphone', 'eerder', 'weer', 'zoeken', 'dienen', 'alleen', 'houden', 'see', 'well', 'good', 'deel', 'find', 'misschien', 'make', 'vinden', 'also', 'manier', 'natuurlijk', 'laten', 'louter', 'komen', 'stellen', 'ergens', 'live', 'ver', 'daarentegen', 'facebook', 'steeds', 'time', 'need', 'enkel', 'new', 'nodig', 'vormen', 'halen', 'duidelijk', 'zeggen', 'camera', 'krijgen', 'brengen', 'eigenlijk', 'proberen', 'gewoon', 'heel', 'zeer', 'telkens', 'look', 'eerst', 'belangrijk', 'nochtans', 'waarmee', 'lang', 'zeker']
# more_words = more_words
# stop_words = list(set(stop_words + more_words))
len(stop_words)

280

In [5]:
def stopwords_preprocess(stop_words):
    for stop in stop_words:
        sent = gensim.utils.simple_preprocess(str(stop.strip()), deacc=True)
        if sent:
            yield(sent)
            
stop_words += ['zoals']
stop_words = [' '.join(w) for w in list(stopwords_preprocess(stop_words))]

'en' in stop_words

True

preprocess to get a (short) list

In [8]:
# nl only            
data = df_grote_word_doc.text.values.tolist()

def only_nl(texts):
    for text in texts:
        lang, _ = classify(text)
        if lang == 'nl':
            yield text
            
def preprocess_and_stopwords(texts):
    for text in texts:
        text_list = []
        for word in simple_preprocess(text, deacc=True):
            if word not in stop_words:
                text_list.append(word)
        yield str(' '.join(text_list))

nl_text = list(only_nl(data))

preprocessed_data = list(preprocess_and_stopwords(nl_text))

len(preprocessed_data), len(nl_text)

(3152, 3152)

In [9]:
# nl + en
preprocessed_data_all = list(preprocess_and_stopwords(data))

len(preprocessed_data_all)

3522

# Embed

In [51]:
sentence_model = SentenceTransformer('sentence-transformers/paraphrase-multilingual-MiniLM-L12-v2')
embeddings = sentence_model.encode(preprocessed_data, show_progress_bar=True)

Batches:   0%|          | 0/99 [00:00<?, ?it/s]

In [10]:
# all
sentence_model = SentenceTransformer('sentence-transformers/paraphrase-multilingual-MiniLM-L12-v2')
embeddings = sentence_model.encode(preprocessed_data_all, show_progress_bar=True)

Batches:   0%|          | 0/111 [00:00<?, ?it/s]

In [52]:
embeddings.shape

(3152, 384)

In [11]:
import sys
sys.getsizeof(embeddings) / 1000000 # in KB

5.40992

# Using kmeans + t-SNE

Embeddings make it better. But the clusters still don't look great.

In [84]:
true_k = 35

model = KMeans(n_clusters=true_k, init="k-means++", max_iter=300, n_init='auto')

model.fit(embeddings)

labels = model.labels_

In [82]:
# Perform t-SNE dimensionality reduction
tsne_model = TSNE(n_components=2, 
                  random_state=20, 
                  learning_rate='auto', # 10 is small and 200 is large (but fast)
                  angle=.99, 
                  # init="random",
                  init='pca',
                  perplexity=40, 
                  early_exaggeration=70)

low_dim_data = tsne_model.fit_transform(np.array(embeddings))

In [9]:
from bokeh.models import ColumnDataSource, HoverTool, TapTool, CustomJS, Div
from bokeh.layouts import column

output_notebook()
mycolors = np.array(list(mcolors.TABLEAU_COLORS.values()) + \
         [mcolors.to_hex(c) for c in plt.cm.Pastel1.colors] + \
         [mcolors.to_hex(c) for c in plt.cm.Set1.colors])

source = ColumnDataSource(data=dict(
    x=low_dim_data[:, 0],
    y=low_dim_data[:, 1],
    colors=mycolors[labels % len(mycolors)],
    onderwerp=[s[:250] for s in preprocessed_data],
    description=preprocessed_data,
    # keywords = keyword_list
    )
                          )

hover = HoverTool()
hover.tooltips = [("onderwerp", "@onderwerp"),
                #   ("keywords", "@keywords")
                  ]

description_div = Div(text="", width=1200, height=200)

callback = CustomJS(args=dict(source=source, div=description_div), code="""
    const indices = source.selected.indices;
    if (indices.length == 0)
        return;
    const desc = source.data['description'][indices[0]];
    div.text = desc;
""")
tap_tool = TapTool(callback=callback)

plot = figure(tools="wheel_zoom, reset", title=f"t-SNE Clustering of {true_k} KMeans Topics", width=1000, height=700)
plot.add_tools(hover)
plot.add_tools(tap_tool)

plot.scatter('x', 'y', source=source, color='colors', size=8)

layout = column(plot, description_div)

show(layout)

Loading BokehJS ...

# BERTopic

In [100]:
# more basic
topic_model2 = BERTopic()
topics2, probs2 = topic_model2.fit_transform(preprocessed_data)

topic_model2.get_topic_info()

Topic  Count                                               Name  \
0      -1   1373                               -1_we_onze_wel_leven   
1       0    323                       0_leven_liefde_gelukkig_punt   
2       1    231                           1_we_leven_mensen_wereld   
3       2    161                  2_we_sociale_economie_economische   
4       3    114                      3_porno_seks_seksuele_beelden   
5       4     70                  4_facebook_vrienden_media_sociale   
6       5     59      5_psychologie_empathie_psychologische_anderen   
7       6     54                   6_blog_blogs_johannes_hyperlinks   
8       7     53                            7_media_tv_we_reflectie   
9       8     48           8_personage_personages_verteller_verhaal   
10      9     48                9_nietzsche_onze_causaliteit_geloof   
11     10     43                   10_marketing_economy_product_the   
12     11     40               11_internet_online_cyberspace_welkom   
13     12     32               12_foto_camera_powell_subjectiviteit   
14     13     32                        13_mensen_alle_heel_reclame   
15     14     30             14_attitude_attitudes_motivatie_gedrag   
16     15     27                    15_film_films_subcultuur_dromen   
17     16     23                16_europa_europese_ich_geschiedenis   
18     17     22             17_technologie_verlangen_innovatie_etc   
19     18     22                      18_netwerk_jouw_net_netwerken   
20     19     22           19_computers_smartphone_universum_iphone   
21     20     21                   20_humor_flirten_keurslijf_ofwel   
22     21     20               21_sociale_zakkenman_dialogen_mensen   
23     22     19                  22_impact_investing_korys_finance   
24     23     19                23_taal_vanuit_verzerkeren_metafoor   
25     24     17        24_plot_plots_reversibiliteit_kwijtschelden   
26     25     16                    25_matthieu_betti_steffen_koken   
27     26     16                  26_drama_minuten_lopen_betrekking   
28     27     15           27_land_landen_basisinkomen_gegarandeerd   
29     28     14                   28_taal_poetische_frans_poetisch   
30     29     14             29_kunst_meebracht_kunstvorm_besteding   
31     30     14                    30_hipsters_hipster_anti_kledij   
32     31     13                31_god_cultuur_organisaties_gelovig   
33     32     13   32_alcohol_singularity_conversaties_koffiemensen   
34     33     13  33_architectuur_architecturale_kwaliteit_benjamin   
35     34     13       34_couchsurfing_couchsurfers_sekte_ontvangen   
36     35     12          35_talent_communiceren_schrijven_manieren   
37     36     12                   36_fantasie_danste_liefde_voyeur   
38     37     12                    37_dj_muziek_muzikale_popmuziek   
39     38     11             38_reverse_design_principe_terugvoeren   
40     39     11                    39_facebook_foto_vrienden_delen   
41     40     10             40_culturen_gefaalde_objectivatie_anti   
42     41     10                 41_burgers_orakel_spoorweg_snowden   
43     42     10    42_hoofdstuk_hoofdpersonages_draft_uitschrijven   

                                       Representation  \
0   [we, onze, wel, leven, mensen, wereld, denken,...   
1   [leven, liefde, gelukkig, punt, goed, waar, da...   
2   [we, leven, mensen, wereld, gaan, wel, waar, o...   
3   [we, sociale, economie, economische, sociaal, ...   
4   [porno, seks, seksuele, beelden, drugs, vrouw,...   
5   [facebook, vrienden, media, sociale, zien, jez...   
6   [psychologie, empathie, psychologische, andere...   
7   [blog, blogs, johannes, hyperlinks, korte, eer...   
8   [media, tv, we, reflectie, onze, via, radio, m...   
9   [personage, personages, verteller, verhaal, pl...   
10  [nietzsche, onze, causaliteit, geloof, eenword...   
11  [marketing, economy, product, the, we, gifting...   
12  [internet, online, cyberspace, welkom, waar, n...   
13  [foto,

In [13]:
topic_model = BERTopic().fit(preprocessed_data_all, embeddings) # all
keywords = topic_model.generate_topic_labels()
labels = np.array(topic_model.topics_)

In [14]:
hierarchical_topics = topic_model.hierarchical_topics(preprocessed_data_all)
topic_model.visualize_hierarchy(hierarchical_topics=hierarchical_topics)

100%|██████████| 46/46 [00:00<00:00, 115.51it/s]


In [16]:
print(topic_model.get_topic_tree(hierarchical_topics))

.
├─seks_porno_mannen_droom_vrouwen
│    ├─angst_cultuur_god_onze_wij
│    │    ├─argentinie_hipsters_hipster_wir_dronken
│    │    │    ├─■──argentinie_espanol_voy_zeer_argentijnse ── Topic: 36
│    │    │    └─hipsters_hipster_wir_dronken_feestje
│    │    │         ├─■──hipsters_hipster_bobo_anti_kledij ── Topic: 37
│    │    │         └─■──wir_feestje_dronken_manufacturing_date ── Topic: 31
│    │    └─angst_god_cultuur_onze_wij
│    │         ├─god_cultuur_onze_moslims_wij
│    │         │    ├─cultuur_onze_moslims_traditie_wij
│    │         │    │    ├─■──culturen_cultuur_identiteit_whitehouse_dier ── Topic: 46
│    │         │    │    └─moslims_onze_traditie_wij_cultuur
│    │         │    │         ├─■──moslims_onze_wij_moeten_individuen ── Topic: 45
│    │         │    │         └─■──moraal_traditie_leerkracht_leerkrachten_nihilisme ── Topic: 26
│    │         │    └─■──god_goden_theisme_gods_pan ── Topic: 40
│    │         └─angst_emoties_kind_pijn_zorgen
│    │             

In [195]:
topic_model.get_representative_docs(2)

['weten geloven jij filosofiestudie beoogde doorgaans eerder gesuggereerd vluchtig gepolst volledige naiviteit vraag zelden ontsloten schijnt eenduidig antwoord houden doordringend besef alle levensvragen ineens oplossen zeker uitgesproken vraag sluimert eerder achtergrond terughoudende verwondering heimelijke verwachting waarvan kiem vraag meegegeven opschorting opdat kiem bloeien eerste realisatie gemaakt oprecht filosofisch verlangen zekerheid laat nooit nimmer bevredigen zeker geloof zoektocht waarheid houdt eerder opschorting tussen haakjes zetten alle gangbare zekerheden waarmee we leven waarmee we dag aanraking komen vanzelfsprekend vinden allemaal tijdelijk locaal contextueel we denken handelen we aangaande ware losgelaten voelen we verwondering wortel vatten we voelen ontluiken loskomen onbevraagde decor vormt bestaan kiem filosofische verwondering datgeen voren treedt sfeer vanzelfsprekend plek licht openbaarheid bemachtigd waar vervolgens ingang vindt onze rede menselijke zi

# Dimensionality reduction with UMAP

In [17]:
reduced_embeddings = UMAP(n_neighbors=10, n_components=2, min_dist=0.0, metric='cosine').fit_transform(embeddings)

## Visualise hierarchical docs

> ignore

In [62]:
# Run the visualization with the original embeddings
topic_model.visualize_hierarchical_documents(preprocessed_data,
                                             hierarchical_topics, 
                                            #  sample=0.5, 
                                            #  nr_levels=3, 
                                             hide_annotations=True, 
                                             hide_document_hover=False, 
                                             reduced_embeddings=np.array(reduced_embeddings)
                                            #  embeddings=np.array(embeddings)
                                             )

`visualize_hierarchical_documents` shows the most importants topics across all documents as layers. 


I think I'll get better along with `TSNE > bokah`.

## Visualise t-SNE

In [18]:
np.unique(filtered_new_labels)

NameError: name 'filtered_new_labels' is not defined

In [22]:
# Perform t-SNE dimensionality reduction
tsne_model = TSNE(n_components=2, 
                  random_state=20, 
                  learning_rate='auto', # 10 is small and 200 is large (but fast)
                  angle=.99, 
                  # init="random",
                  init='pca',
                  perplexity=40, 
                  early_exaggeration=100)

low_dim_data = tsne_model.fit_transform(np.array(reduced_embeddings))

In [23]:
len(low_dim_data)

3522

### `Masking`

In [230]:
new_labels = []
for label in labels:
    if label in [0, 1, 36]:
        new_labels.append(-1)
    else:
        new_labels.append(label)
        
new_labels = np.array(new_labels)

# to filter, use this np magic (also works in pandas)
mask = new_labels != -1

filtered_x = low_dim_data[:, 0][mask]
filtered_y = low_dim_data[:, 1][mask]
filtered_new_labels = new_labels[mask]

len(filtered_x), len(filtered_new_labels)

(1521, 1521)

In [244]:
np.isin(labels, [-1, 0, 1, 36], invert=True).sum()

1521

In [345]:
# inintuitive but good: np.isin give True or False 
mask = np.isin(labels, [-1, 0, 1, 2, 36], invert=True)

# Filter low_dim_data and new_labels using the mask
filtered_low_dim_data = low_dim_data[mask]
filtered_labels = labels[mask]

# and for later processing
filtered_df_topic_model = df_topic_model[mask]
filtered_text = np.array(nl_text)[mask]

len(filtered_df_topic_model), len(low_dim_data), len(filtered_labels)

(1386, 1521, 1386)

# Plotting in bokeh

In [460]:
curdoc().clear()

In [445]:
curdoc().validate()

In [20]:
type(preprocessed_data_all)

list

In [24]:
from bokeh.models import ColumnDataSource, HoverTool, TapTool, CustomJS, Div
from bokeh.layouts import column
from bokeh.plotting import curdoc

output_notebook()

mycolors = np.array(list(mcolors.TABLEAU_COLORS.values()) + \
            [mcolors.to_hex(c) for c in plt.cm.Pastel1.colors] + \
            [mcolors.to_hex(c) for c in plt.cm.Pastel2.colors] + \
            [mcolors.to_hex(c) for c in plt.cm.Paired.colors]
            )

source = ColumnDataSource(data=dict(
    x=low_dim_data[:,0],
    y=low_dim_data[:,1],
    colors=mycolors[labels % len(mycolors)],
    onderwerp=[s[:80] + "..." for s in np.array(preprocessed_data_all)],
    description=np.array(preprocessed_data_all), 
    keywords = np.array(keywords)[labels]
    ))

hover = HoverTool()
hover.tooltips = """
<div>
    <span style="font-size: 15px;">@keywords</span>&nbsp;
</div>
<div>
    <span style="font-size: 10px; color: #666;">@onderwerp</span>
</div>
"""

description_div = Div(text="", width=1200, height=50)

callback = CustomJS(args=dict(source=source, div=description_div), code="""
    const indices = source.selected.indices;
    if (indices.length == 0)
        return;
    const desc = source.data['description'][indices[0]];
    div.text = desc;
""")

tap_tool = TapTool(callback=callback)

curdoc().theme = 'dark_minimal' # 'night_sky'

plot = figure(tools="wheel_zoom, reset", 
              title=f"t-SNE Clustering of {len(keywords)} Topics", 
              width=1100, height=700)

plot.circle('x', 'y', source=source, color='colors', fill_alpha=0.2, size=10)
plot.add_tools(hover)
plot.add_tools(tap_tool)

layout = column(plot, description_div) # , sizing_mode='stretch_both') 

show(layout, notebook_handle=True)

Loading BokehJS ...

# Inspecting the docs and topics

In [29]:
df_topic_model = topic_model.get_document_info(preprocessed_data_all)

Main stats per topic

In [27]:
topic_model.get_topic_info().head()

Topic  Count                                     Name  \
0     -1   1465                -1_onze_mensen_wel_wereld   
1      0    165  0_wetenschap_intelligentie_onze_reality   
2      1    148          1_geld_sociale_sociaal_ethische   
3      2    127               2_liefde_love_relatie_feel   
4      3    120               3_facebook_fb_bda_vanavond   

                                      Representation  \
0  [onze, mensen, wel, wereld, leven, waar, enkel...   
1  [wetenschap, intelligentie, onze, reality, fil...   
2  [geld, sociale, sociaal, ethische, moeten, eco...   
3  [liefde, love, relatie, feel, romantische, fee...   
4  [facebook, fb, bda, vanavond, vrienden, online...   

                                 Representative_Docs  
0  [perplexiteit amputatie lullig velletje idee w...  
1  [blog filosofieclan zie sept ongetwijfeld sleu...  
2  [stanford tekst distributive justice overheden...  
3  [dearest rosy love love much love like love lo...  
4  [fbprofiel staan bril baard groepje sta liefst...

All topic names - useful for masking!

In [30]:
df_topic_model_sorted = df_topic_model.sort_values(by='Topic')
', '.join(df_topic_model_sorted["Name"].unique())

'-1_onze_mensen_wel_wereld, 0_wetenschap_intelligentie_onze_reality, 1_geld_sociale_sociaal_ethische, 2_liefde_love_relatie_feel, 3_facebook_fb_bda_vanavond, 4_muziek_dj_music_muzikale, 5_europa_frankrijk_europese_land, 6_voelde_kamer_bed_ogen, 7_porno_seks_seksuele_masturberen, 8_boek_schrijver_schrijven_lezen, 9_blog_blogs_johannes_eerste, 10_impact_social_business_innovatie, 11_stad_road_car_cyclists, 12_reizen_droom_reis_travel, 13_droom_dromen_slaap_denken, 14_taal_spreken_discours_woorden, 15_beelden_kunst_beeld_taal, 16_internet_zoeken_netwerk_verkeerde, 17_empathy_empathie_anderen_schaamte, 18_overtuigen_gedrag_denken_kritiek, 19_personage_personages_verteller_schouwspel, 20_lage_opvattingen_erkenning_hoog, 21_angst_emoties_pijn_zorgen, 22_leven_verleiding_overgrootouders_orde, 23_klimmen_wanneer_berg_meter, 24_seks_meisjes_steffen_erotiek, 25_mannen_vrouwen_mannelijke_vrouw, 26_moraal_traditie_leerkracht_leerkrachten, 27_mannen_vrouw_homo_kussen, 28_vrienden_beleefd_vriendscha

Alternative way of getting representative docs per topic

In [347]:
df_representative_docs = pd.DataFrame({"Document": nl_text, "Topic": topic_model.topics_})
df_representative_docs.sort_values(by='Topic')[df_topic_model["Topic"] > 0]

Document  Topic
2026  Voor S. De mens heeft zichzelf gedomesticeerd....      1
2016  Bij verschillende diersoorten wordt er enkel g...      1
2154  Ik had er met Rosy over: veel meisjes hebben e...      1
1565  ik ben gefascineerd in hoeverre schoonheid van...      1
2731  Lang heb ik seks in een continuüm gezien, met ...      1
...                                                 ...    ...
578   Met die glimlach kijk je in de toekomst - door...     36
832   Een jaar of 40 geleden kwam de commerciële fot...     36
1591  Eerst was er de mechanische reproductie van be...     36
1677  G:\Mijn afbeeldingen\_ reis (van laptop)\20-7-...     36
2414  In een artikel over een foto genomen in 1865 w...     36

[1759 rows x 2 columns]

In [260]:
filtered_df_topic_model.head()

Document  Topic  \
0  net dagboek auteur discours ontwikkelen boek n...     11   
1  bepaalde vragen rond structuur verhaallijn hou...     24   
2  drugs ziekte gemoed zekere zin stemmingen late...     30   
3  notie overdenken waard zonet kwam conclusie ho...     21   
4  taal taal lijn boven treinsporen loopt machine...     11   

                                  Name  \
0       11_taal_spreken_discours_zeker   
1        24_fictie_realiteit_wensen_we   
2           30_drugs_mdma_jake_persoon   
3  21_overtuigen_gedrag_denken_kritiek   
4       11_taal_spreken_discours_zeker   

                                      Representation  \
0  [taal, spreken, discours, zeker, woorden, dial...   
1  [fictie, realiteit, wensen, we, onze, wereld, ...   
2  [drugs, mdma, jake, persoon, coke, middelen, d...   
3  [overtuigen, gedrag, denken, kritiek, weerlegg...   
4  [taal, spreken, discours, zeker, woorden, dial...   

                                 Representative_Docs  \
0  [engelstalige blog sensibiliteiten talen leren...   
1  [onderscheid tussen realiteit fictie scherper ...   
2  [drugs ziekte gemoed zekere zin stemmingen lat...   
3  [subjectiviteit objectiviteit meest subjectief...   
4  [engelstalige blog sensibiliteiten talen leren...   

                                         Top_n_words  Probability  \
0  taal - spreken - discours - zeker - woorden - ...     0.576662   
1  fictie - realiteit - wensen - we - onze - were...     1.000000   
2  drugs - mdma - jake - persoon - coke - middele...     0.800917   
3  overtuigen - gedrag - denken - kritiek - weerl...     0.901110   
4  taal - spreken - discours - zeker - woorden - ...     0.803940   

   Representative_document  
0                     True  
1                    False  
2                     True  
3                    False  
4                    False

In [421]:
filtered_df_topic_model['texts'] = filtered_text

In [36]:
# ALL
df_topic_model['texts'] = data

In [336]:
len(reduced_embeddings), len(mask)

(3152, 3152)

In [339]:
reduced_embeddings[0]

array([3.4128726, 2.184821 ], dtype=float32)

In [423]:
filtered_df_topic_model['2d_embeddings_x'] = reduced_embeddings[mask][:,0]
filtered_df_topic_model['2d_embeddings_y'] = reduced_embeddings[mask][:,1]

In [31]:
# all
df_topic_model['2d_embeddings_x'] = reduced_embeddings[:,0]
df_topic_model['2d_embeddings_y'] = reduced_embeddings[:,1]

# Save as pickle

In [37]:
df_topic_model.to_pickle("df_topic_model_all")

# Generate text based on a random sample of docs  

In [333]:
# choose a topic
topic_nr = 4

n_fragments = 3

# get a sample of fragmetns
fragments = filtered_df_topic_model['texts'][filtered_df_topic_model['Topic'] == topic_nr].sample(n_fragments).values.tolist()

fragments_str = "- " + "\n\n- ".join([fragment[:2000] + "..." for fragment in fragments])

print(fragments_str)

- Er wordt niet meer in de spiegel van onze eigen menselijkheid gekeken, er wordt op de maatschappij toegekeken, op de bestaande hiërarchieën en verdelingen van wat dan ook.
...

- wat wij kunnen doen om het lot van de zuid-amerikanen te verbeteren:
-globale agrarische hervormingen ondersteunen
-stages en opleidingen van latinos in europa makkelijker maken
-locale banken die leningen aan lage rentes opzetten
...

- Het is gek hoezeer de Engelsen trouw zijn aan traditie en tegelijkertijd zo nauw verbonden met de voortbrengselen van een globaal kapitalisme. Het beloofde land van Amerika, Australië, Nieuw-Zeeland en Zuid-Afrika lijken heel wat minder ver weg.
De vraag die Rosy’s moeder altijd stelt, is tekenend: “En wat is bij jou de traditionele kerstmiscake?” Zou het kunnen dat de hang naar traditie er als reactie gekomen is op de confrontatie met de vele andere tradities?
Het nauwlettend bewaren van tradities en huldigen van zaken waarover men fier kan zijn, maakt de identiteit uit. De

In [334]:
import openai
response = openai.ChatCompletion.create(
                            model="gpt-3.5-turbo-0613", # "gpt-4",
                            messages=[
                                {"role": "system", "content": "De gebruiker heeft enkele fragmenten geschreven. Verbindt ze in één samenhangende paragraaf."},
                                {"role": "user", "content": fragments_str}],
                            stream=True,
                            max_tokens=512,)

for res in response:
    content_chunk = res.choices[0].delta.get("content", "")
    print(content_chunk, end='')

De huidige maatschappij lijkt steeds meer gericht te zijn op het extern observeren van de wereld om ons heen, in plaats van dat we nog naar onszelf kijken als mens. We kijken naar de bestaande hiërarchieën en verdelingen in de maatschappij, zonder ons af te vragen wat wij kunnen doen om het lot van anderen te verbeteren. Bijvoorbeeld, in het geval van de zuid-Amerikanen, zouden we globale agrarische hervormingen kunnen ondersteunen, stages en opleidingen van latinos in europa makkelijker kunnen maken en locale banken kunnen oprichten die leningen aan lage rentes verstrekken. Het is opmerkelijk hoe trouw de Engelsen zijn aan traditie, terwijl ze tegelijkertijd sterk verbonden zijn met het globale kapitalisme. Landen zoals Amerika, Australië, Nieuw-Zeeland en Zuid-Afrika lijken dichterbij dan ooit te zijn. Deze confrontaties met andere tradities kunnen een reactie hebben uitgelokt, waarbij mensen de behoefte voelen om hun eigen tradities te behouden en te eren. Het vasthouden aan traditi